# 04c - Dataset UC2 Épidémio : Granularité Usager

---

## Objectif

Créer un dataset à **granularité usager** pour l'analyse épidémiologique (UC2) :

1. **Jointure** des features accident (03a) avec la table USAGERS via `Num_Acc`
2. **Création de features individuelles** (âge, sexe, type d'usager, équipement)
3. **Target individuelle** : `grave_usager` (l'usager est tué ou hospitalisé)
4. **Datasets progressifs** V1 → V3

## Pourquoi la granularité usager ?

| Aspect | Niveau Accident (04b) | Niveau Usager (04c) |
|--------|----------------------|---------------------|
| **Granularité** | 1 ligne = 1 accident | 1 ligne = 1 usager |
| **Volume** | ~208k lignes | ~477k lignes |
| **Target** | `grave` (35.4%) | `grave_usager` (17.7%) |
| **Ratio** | 1:1.8 | 1:4.7 |
| **Avantage** | Vue macro | Facteurs individuels |
| **Features spécifiques** | - | Âge, sexe, ceinture, rôle |

> **Note** : Le passage au niveau usager **dilue le signal** (17.7% vs 35.4%) mais apporte des features individuelles très prédictives (`ceinture` = corrélation #1 du dataset).

## Données

- **Input** : `dataset_features_intelligentes.csv` (208,616 × 50) + fichiers `usagers-YYYY.csv`
- **Output** : `UC2_usager_v1_demo.csv`, `UC2_usager_v2_comportement.csv`, `UC2_usager_v3_complet.csv`
- **Notebook précédent** : `04b_dataset_UC2.ipynb` (granularité accident)
- **Notebook suivant** : `05b_model_UC2_epidemio.ipynb`

In [1]:
import pandas as pd
import numpy as np
from pathlib import Path
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import warnings
warnings.filterwarnings('ignore')

import plotly.io as pio
pio.templates.default = "plotly_white"

DATA_DIR = Path("../../../data")

USAGERS_FILES = {
    2021: 'usagers-2021.csv',
    2022: 'usagers-2022.csv',
    2023: 'usagers-2023.csv',
    2024: 'usagers-2024.csv',
}

ANNEES = [2021, 2022, 2023, 2024]

print("Configuration chargée")

Configuration chargée


---

## 1. Chargement des data

Deux sources :
- **Features accident** : `dataset_features_intelligentes.csv` (208,616 accidents, 50 colonnes dont `Num_Acc`)
- **Usagers bruts** : `usagers-YYYY.csv` (4 années, ~507k usagers)

In [2]:
# === Features accident (03a) ===
df_features = pd.read_csv(DATA_DIR / 'dataset_features_intelligentes.csv')
print(f"Features accident chargées : {df_features.shape}")
print(f"Num_Acc présent : {'Num_Acc' in df_features.columns}")
print(f"Num_Acc uniques : {df_features['Num_Acc'].nunique():,}")

# === Usagers bruts (4 années) ===
dfs_usagers = []
print("\n=== CHARGEMENT USAGERS ===")
for annee in ANNEES:
    filepath = DATA_DIR / str(annee) / USAGERS_FILES[annee]
    df_u = pd.read_csv(filepath, sep=';', low_memory=False)
    
    # Sécurité : renommer Accident_Id si présent
    if 'Accident_Id' in df_u.columns and 'Num_Acc' not in df_u.columns:
        df_u = df_u.rename(columns={'Accident_Id': 'Num_Acc'})
    
    df_u['annee'] = annee
    dfs_usagers.append(df_u)
    print(f"  {annee} : {len(df_u):,} usagers")

usagers = pd.concat(dfs_usagers, ignore_index=True)
print(f"\n  TOTAL : {len(usagers):,} usagers")
print(f"  Colonnes : {list(usagers.columns)}")
print(f"  Num_Acc uniques (usagers) : {usagers['Num_Acc'].nunique():,}")

Features accident chargées : (208616, 50)
Num_Acc présent : True
Num_Acc uniques : 208,616

=== CHARGEMENT USAGERS ===
  2021 : 129,248 usagers
  2022 : 126,662 usagers
  2023 : 125,789 usagers
  2024 : 125,187 usagers

  TOTAL : 506,886 usagers
  Colonnes : ['Num_Acc', 'id_usager', 'id_vehicule', 'num_veh', 'place', 'catu', 'grav', 'sexe', 'an_nais', 'trajet', 'secu1', 'secu2', 'secu3', 'locp', 'actp', 'etatp', 'annee']
  Num_Acc uniques (usagers) : 221,044


### Observation : Données chargées

- **Features accident** : 208,616 × 50 colonnes, `Num_Acc` confirmé présent
- **Usagers bruts** : 506,886 usagers sur 4 ans, stable (~125-129k/an)
- **Num_Acc uniques (usagers)** : 221,044 = total accidents avant filtre métropole ✓

**Ratio usagers/accidents** : 506,886 / 221,044 = **2.29 usagers/accident** en moyenne.
Ce ratio est cohérent (2 véhicules × ~1.15 occupants par véhicule + piétons).

---

## 2. Préparation des features usager

### Codes BAAC usagers

| Variable | Codes | Usage |
|----------|-------|-------|
| `grav` | 1=Indemne, 2=Tué, 3=Hospitalisé, 4=Blessé léger | → Target `grave_usager` |
| `catu` | 1=Conducteur, 2=Passager, 3=Piéton | → Features binaires |
| `sexe` | 1=Masculin, 2=Féminin | → `homme` |
| `an_nais` | Année de naissance | → `age`, catégories |
| `secu1` | 1=Ceinture, 2=Casque, 3=Dispositif enfant, 4=Gilet, 9=Autre | → Équipement |
| `trajet` | 1=Dom-travail, 2=Dom-école, 3=Courses, 4=Pro, 5=Loisirs | → Motif |

In [3]:
# === TARGET USAGER ===
# grav: 1=Indemne, 2=Tué, 3=Hospitalisé, 4=Blessé léger
usagers['grave_usager'] = usagers['grav'].isin([2, 3]).astype(int)

# Distribution de la gravité
print("="*60)
print("DISTRIBUTION DE LA GRAVITÉ PAR USAGER")
print("="*60)
grav_labels = {1: 'Indemne', 2: 'Tué', 3: 'Hospitalisé', 4: 'Blessé léger', -1: 'Non renseigné'}
grav_dist = usagers['grav'].map(grav_labels).fillna('Autre').value_counts().sort_index()
for label, count in grav_dist.items():
    pct = count / len(usagers) * 100
    print(f"  {label:<20}: {count:>8,} ({pct:>5.1f}%)")

print(f"\nTarget grave_usager : {usagers['grave_usager'].sum():,} / {len(usagers):,} ({usagers['grave_usager'].mean()*100:.1f}%)")
ratio = (1 - usagers['grave_usager'].mean()) / usagers['grave_usager'].mean()
print(f"Ratio négatifs:positifs = 1:{ratio:.1f}")

DISTRIBUTION DE LA GRAVITÉ PAR USAGER
  Blessé léger        :  201,026 ( 39.7%)
  Hospitalisé         :   76,750 ( 15.1%)
  Indemne             :  215,092 ( 42.4%)
  Non renseigné       :      419 (  0.1%)
  Tué                 :   13,599 (  2.7%)

Target grave_usager : 90,349 / 506,886 (17.8%)
Ratio négatifs:positifs = 1:4.6


In [4]:
# === ÂGE ===
# Utiliser l'année de l'accident (pas aujourd'hui) pour un âge exact
usagers['age'] = usagers['annee'] - usagers['an_nais']

# Nettoyer les valeurs aberrantes
usagers.loc[usagers['an_nais'].isin([-1, 0]), 'age'] = np.nan
usagers.loc[(usagers['age'] < 0) | (usagers['age'] > 110), 'age'] = np.nan

n_age_missing = usagers['age'].isna().sum()
pct_missing = n_age_missing / len(usagers) * 100
age_median = usagers['age'].median()
usagers['age'] = usagers['age'].fillna(age_median)

print(f"Âge : {n_age_missing:,} valeurs manquantes ({pct_missing:.1f}%) → imputées par médiane ({age_median:.0f} ans)")
print(f"Âge moyen  : {usagers['age'].mean():.1f} ans")
print(f"Âge médian : {usagers['age'].median():.0f} ans")
print(f"Min-Max    : {usagers['age'].min():.0f} - {usagers['age'].max():.0f} ans")

# === CATÉGORIES D'ÂGE ===
usagers['age_18_24'] = usagers['age'].between(18, 24).astype(int)
usagers['age_65_plus'] = (usagers['age'] >= 65).astype(int)

# === SEXE ===
usagers['homme'] = (usagers['sexe'] == 1).astype(int)

# === TYPE D'USAGER ===
usagers['conducteur'] = (usagers['catu'] == 1).astype(int)
usagers['passager'] = (usagers['catu'] == 2).astype(int)
usagers['pieton_usager'] = (usagers['catu'] == 3).astype(int)

# === ÉQUIPEMENT DE SÉCURITÉ ===
# secu1 nettoyage : convertir en numérique
usagers['secu1'] = pd.to_numeric(usagers['secu1'], errors='coerce')
usagers['ceinture'] = (usagers['secu1'] == 1).astype(int)
usagers['casque'] = (usagers['secu1'] == 2).astype(int)
usagers['sans_protection'] = (~usagers['secu1'].isin([1, 2, 3, 4])).astype(int)

# === TRAJET ===
usagers['trajet'] = pd.to_numeric(usagers['trajet'], errors='coerce')
usagers['trajet_domicile_travail'] = usagers['trajet'].isin([1, 2]).astype(int)
usagers['trajet_loisir'] = (usagers['trajet'] == 5).astype(int)

# === RÉCAPITULATIF ===
print("\n" + "="*60)
print("FEATURES USAGER CRÉÉES")
print("="*60)

user_features_demo = ['age', 'homme', 'conducteur', 'passager', 'pieton_usager', 'age_18_24', 'age_65_plus']
user_features_comportement = ['ceinture', 'casque', 'sans_protection', 'trajet_domicile_travail', 'trajet_loisir']

print("\nDémographie :")
for feat in user_features_demo:
    if usagers[feat].nunique() <= 2:
        n = int(usagers[feat].sum())
        pct = usagers[feat].mean() * 100
        print(f"  {feat:<25}: {n:>8,} ({pct:>5.1f}%)")
    else:
        print(f"  {feat:<25}: mean={usagers[feat].mean():.1f}, median={usagers[feat].median():.0f}")

print("\nComportement / Équipement :")
for feat in user_features_comportement:
    n = int(usagers[feat].sum())
    pct = usagers[feat].mean() * 100
    print(f"  {feat:<25}: {n:>8,} ({pct:>5.1f}%)")

Âge : 11,118 valeurs manquantes (2.2%) → imputées par médiane (35 ans)
Âge moyen  : 38.5 ans
Âge médian : 35 ans
Min-Max    : 0 - 110 ans

FEATURES USAGER CRÉÉES

Démographie :
  age                      : mean=38.5, median=35
  homme                    :  338,907 ( 66.9%)
  conducteur               :  377,740 ( 74.5%)
  passager                 :   91,141 ( 18.0%)
  pieton_usager            :   38,005 (  7.5%)
  age_18_24                :   95,408 ( 18.8%)
  age_65_plus              :   54,637 ( 10.8%)

Comportement / Équipement :
  ceinture                 :  295,580 ( 58.3%)
  casque                   :   89,855 ( 17.7%)
  sans_protection          :  118,059 ( 23.3%)
  trajet_domicile_travail  :   77,041 ( 15.2%)
  trajet_loisir            :  183,216 ( 36.1%)


### Observation : Features usager créées

**Target `grave_usager`** : 90,349 / 506,886 (**17.8%**, ratio 1:4.6)

Changement majeur par rapport au niveau accident :

| Niveau | Target | Taux | Ratio |
|--------|--------|------|-------|
| Accident (04b) | `grave` | 35.4% | 1:1.8 |
| Usager (04c) | `grave_usager` | 17.8% | 1:4.6 |

→ Le taux de gravité est **divisé par 2** au niveau usager. C'est logique : dans un accident "grave", tous les usagers ne sont pas sévèrement blessés. La majorité s'en sort indemne (42.4%) ou avec blessures légères (39.7%).

**⚠️ Conséquence pour la modélisation** : Le ratio 1:4.6 est nettement plus déséquilibré que le 1:1.8 attendu. EasyEnsemble reste adapté mais le déséquilibre est plus marqué.

**Démographie** :
- `homme` = 66.9% → les hommes sont **surreprésentés** (2x) dans les accidents
- `conducteur` = 74.5%, `passager` = 18.0%, `piéton` = 7.5% → total 100% ✓
- Âge médian = 35 ans, 2.2% de valeurs manquantes (acceptable)

**⚠️ Point de vigilance : `sans_protection`** = 23.3%. Ce chiffre inclut les piétons (7.5%, qui par définition ne portent ni ceinture ni casque), les cas non renseignés (secu1=-1) et les "autres" (secu1=9). Ce n'est **pas** "23% de conducteurs sans ceinture". La feature mélange l'absence réelle de protection avec les cas non applicables.

---

## 3. Jointure usagers ↔ features accident

Jointure **inner** sur `Num_Acc` :
- Les features accident (contexte, route, véhicules) sont **dupliquées** pour chaque usager du même accident
- Seuls les accidents de France métropolitaine (208,616) sont conservés
- Relation **1 accident → N usagers** (~2.3 usagers par accident en moyenne)

In [5]:
# Colonnes usager à conserver pour la jointure
cols_usager = ['Num_Acc', 'grave_usager', 'age', 'homme', 'conducteur', 'passager', 
               'pieton_usager', 'age_18_24', 'age_65_plus', 'ceinture', 'casque', 
               'sans_protection', 'trajet_domicile_travail', 'trajet_loisir']

usagers_clean = usagers[cols_usager].copy()

# Features accident (sans les targets accident-level mortel/grave)
features_accident = [c for c in df_features.columns if c not in ['mortel', 'grave']]
df_accident = df_features[features_accident].copy()

# Jointure
print("Jointure usagers ↔ features accident...")
print(f"  Usagers avant jointure  : {len(usagers_clean):,}")
print(f"  Accidents (métropole)   : {len(df_accident):,}")

df = usagers_clean.merge(df_accident, on='Num_Acc', how='inner')

print(f"  Usagers après jointure  : {len(df):,}")
print(f"  Accidents matchés       : {df['Num_Acc'].nunique():,}")
print(f"  Usagers/accident moyen  : {len(df) / df['Num_Acc'].nunique():.2f}")

# Exclus = DOM-TOM
n_exclus = len(usagers_clean) - len(df)
print(f"\n  Usagers exclus (DOM-TOM) : {n_exclus:,} ({n_exclus/len(usagers_clean)*100:.1f}%)")

# Supprimer Num_Acc du dataset final (identifiant, pas une feature)
df = df.drop(columns=['Num_Acc'])

print(f"\n  Dataset final : {df.shape}")
print(f"  Target grave_usager : {df['grave_usager'].sum():,} ({df['grave_usager'].mean()*100:.1f}%)")

Jointure usagers ↔ features accident...
  Usagers avant jointure  : 506,886
  Accidents (métropole)   : 208,616
  Usagers après jointure  : 477,294
  Accidents matchés       : 208,616
  Usagers/accident moyen  : 2.29

  Usagers exclus (DOM-TOM) : 29,592 (5.8%)

  Dataset final : (477294, 60)
  Target grave_usager : 84,329 (17.7%)


### Observation : Jointure

- **477,294 usagers** après jointure (sur 506,886)
- **29,592 exclus** (5.8%) = usagers des DOM-TOM, cohérent avec le filtre métropole des accidents (5.6%)
- **208,616 accidents matchés** = 100% des accidents métropole ✓
- **2.29 usagers/accident** en moyenne
- **Target** : 84,329 graves (17.7%), ratio 1:4.7

Le dataset est **2.3× plus volumineux** que le niveau accident (477k vs 208k), ce qui donne plus de puissance statistique pour détecter les facteurs individuels.

---

## 4. Analyse des features usager

### 4.1 Distribution de la gravité par type d'usager

In [6]:
# Taux de gravité par type d'usager
print("="*70)
print("TAUX DE GRAVITÉ PAR TYPE D'USAGER")
print("="*70)

base_rate = df['grave_usager'].mean() * 100
print(f"{'Type':<25} {'N':>10} {'% Grave':>10} {'Ratio':>8}")
print("-"*55)
print(f"{'BASELINE':<25} {len(df):>10,} {base_rate:>9.1f}% {'1.0x':>8}")
print("-"*55)

user_cats = [
    ('Conducteur', 'conducteur'),
    ('Passager', 'passager'),
    ('Piéton', 'pieton_usager'),
    ('Homme', 'homme'),
    ('Femme (homme=0)', 'homme', True),  # inversé
    ('18-24 ans', 'age_18_24'),
    ('65+ ans', 'age_65_plus'),
    ('Ceinture', 'ceinture'),
    ('Casque', 'casque'),
    ('Sans protection', 'sans_protection'),
    ('Trajet dom-travail', 'trajet_domicile_travail'),
    ('Trajet loisir', 'trajet_loisir'),
]

for item in user_cats:
    if len(item) == 3:  # inversé
        label, col, inv = item
        subset = df[df[col] == 0]
    else:
        label, col = item
        subset = df[df[col] == 1]
    
    n = len(subset)
    rate = subset['grave_usager'].mean() * 100
    ratio = rate / base_rate
    print(f"{label:<25} {n:>10,} {rate:>9.1f}% {ratio:>7.1f}x")

TAUX DE GRAVITÉ PAR TYPE D'USAGER
Type                               N    % Grave    Ratio
-------------------------------------------------------
BASELINE                     477,294      17.7%     1.0x
-------------------------------------------------------
Conducteur                   356,498      16.5%     0.9x
Passager                      84,836      16.4%     0.9x
Piéton                        35,960      32.0%     1.8x
Homme                        319,186      18.9%     1.1x
Femme (homme=0)              158,108      15.1%     0.9x
18-24 ans                     89,843      17.9%     1.0x
65+ ans                       52,450      29.1%     1.6x
Ceinture                     279,945      10.5%     0.6x
Casque                        83,884      33.7%     1.9x
Sans protection              110,242      23.7%     1.3x
Trajet dom-travail            73,424      15.7%     0.9x
Trajet loisir                173,660      24.2%     1.4x


In [7]:
# Visualisation : gravité par type d'usager et âge
fig = make_subplots(
    rows=1, cols=2,
    subplot_titles=['Taux de gravité par type d\'usager', 'Distribution d\'âge par gravité'],
    column_widths=[0.4, 0.6]
)

# Bar chart par type d'usager
types = ['conducteur', 'passager', 'pieton_usager']
labels_types = ['Conducteur', 'Passager', 'Piéton']
rates = [df[df[t] == 1]['grave_usager'].mean() * 100 for t in types]

fig.add_trace(
    go.Bar(
        x=labels_types, y=rates,
        marker_color=['#3498db', '#2ecc71', '#e74c3c'],
        text=[f'{r:.1f}%' for r in rates],
        textposition='outside',
        showlegend=False
    ),
    row=1, col=1
)

# Ligne baseline
fig.add_hline(y=base_rate, line_dash='dash', line_color='gray', 
              annotation_text=f'Baseline {base_rate:.1f}%', row=1, col=1)

# Histogramme d'âge par gravité
for grav_val, name, color in [(0, 'Non grave', '#3498db'), (1, 'Grave', '#e74c3c')]:
    subset = df[df['grave_usager'] == grav_val]
    fig.add_trace(
        go.Histogram(
            x=subset['age'], name=name,
            marker_color=color, opacity=0.6,
            nbinsx=50
        ),
        row=1, col=2
    )

fig.update_layout(height=400, title_text='Analyse usager : type et âge vs gravité', barmode='overlay')
fig.update_yaxes(title_text='% Grave', row=1, col=1)
fig.update_xaxes(title_text='Âge', row=1, col=2)
fig.show()

In [8]:
# Taux de gravité par tranche d'âge (granulaire)
df['tranche_age'] = pd.cut(df['age'], bins=[0, 14, 17, 24, 34, 44, 54, 64, 74, 120],
                           labels=['0-14', '15-17', '18-24', '25-34', '35-44', '45-54', '55-64', '65-74', '75+'])

age_analysis = df.groupby('tranche_age', observed=True).agg(
    n=('grave_usager', 'count'),
    taux_grave=('grave_usager', 'mean')
).reset_index()
age_analysis['taux_grave'] = age_analysis['taux_grave'] * 100

fig = px.bar(
    age_analysis, x='tranche_age', y='taux_grave',
    text=age_analysis['taux_grave'].apply(lambda x: f'{x:.1f}%'),
    color='taux_grave', color_continuous_scale='Reds',
    title='Taux de gravité par tranche d\'âge'
)
fig.add_hline(y=base_rate, line_dash='dash', line_color='gray', annotation_text=f'Baseline {base_rate:.1f}%')
fig.update_layout(height=400, xaxis_title='Tranche d\'âge', yaxis_title='% Grave', showlegend=False)
fig.show()

# Nettoyage colonne temporaire
df = df.drop(columns=['tranche_age'])

### Observation : Analyse par type d'usager et âge

**Taux de gravité par type d'usager** :

| Type | Taux grave | Ratio | Interprétation |
|------|-----------|-------|----------------|
| **Piéton** | **32.0%** | **1.8x** | Le plus vulnérable (absence de carrosserie) |
| Conducteur | 16.5% | 0.9x | Légèrement sous baseline |
| Passager | 16.4% | 0.9x | Similaire au conducteur |

**Facteurs de risque individuels** :
- **65+ ans** : 29.1% (1.6x) → les seniors sont très vulnérables
- **Homme** : 18.9% (1.1x) vs Femme 15.1% (0.9x) → surmortalité masculine modérée

**⚠️ Résultat contre-intuitif : `casque` = 33.7% (1.9x)**

Les porteurs de casque ont un taux de gravité **presque 2x la baseline**. C'est un **paradoxe de Simpson** : le casque est porté par les motards et cyclistes, qui sont intrinsèquement plus vulnérables (pas de carrosserie). Le casque ne *cause* pas la gravité, il est un *proxy* du type de véhicule vulnérable.

**→ Pour la modélisation** : cette corrélation confondante est un risque d'interprétation erronée. Le modèle pourrait utiliser `casque` comme proxy de "deux-roues", ce qui est techniquement correct mais trompeur en termes de causalité.

**Effet protecteur réel** : `ceinture` = 10.5% (0.6x) → l'équipement le plus "protecteur" en apparence, mais là aussi c'est en partie un proxy de "voiture" (vs deux-roues/piéton).

### 4.2 Équipement de sécurité et gravité

In [9]:
# Analyse croisée équipement × type d'usager
print("="*70)
print("ÉQUIPEMENT DE SÉCURITÉ × TYPE D'USAGER → GRAVITÉ")
print("="*70)

# Pour les conducteurs/passagers : ceinture
for role, role_name in [('conducteur', 'Conducteur'), ('passager', 'Passager')]:
    subset = df[df[role] == 1]
    avec_ceinture = subset[subset['ceinture'] == 1]
    sans_ceinture = subset[subset['ceinture'] == 0]
    
    rate_avec = avec_ceinture['grave_usager'].mean() * 100 if len(avec_ceinture) > 0 else 0
    rate_sans = sans_ceinture['grave_usager'].mean() * 100 if len(sans_ceinture) > 0 else 0
    
    print(f"\n{role_name} :")
    print(f"  Avec ceinture : {len(avec_ceinture):>8,} → {rate_avec:.1f}% grave")
    print(f"  Sans ceinture : {len(sans_ceinture):>8,} → {rate_sans:.1f}% grave")
    if rate_avec > 0:
        print(f"  Ratio sans/avec : {rate_sans/rate_avec:.1f}x")

# Visualisation
equip_data = []
for equip, equip_name in [('ceinture', 'Ceinture'), ('casque', 'Casque'), ('sans_protection', 'Sans protection')]:
    for val, val_name in [(1, 'Oui'), (0, 'Non')]:
        subset = df[df[equip] == val]
        if len(subset) > 100:  # seuil minimum
            rate = subset['grave_usager'].mean() * 100
            equip_data.append({'Équipement': f'{equip_name} = {val_name}', 'Taux grave (%)': rate, 'N': len(subset)})

df_equip = pd.DataFrame(equip_data)

fig = px.bar(
    df_equip, x='Équipement', y='Taux grave (%)',
    color='Taux grave (%)', color_continuous_scale='Reds',
    text=df_equip['Taux grave (%)'].apply(lambda x: f'{x:.1f}%'),
    title='Taux de gravité par équipement de sécurité'
)
fig.add_hline(y=base_rate, line_dash='dash', line_color='gray', annotation_text=f'Baseline {base_rate:.1f}%')
fig.update_layout(height=400, showlegend=False)
fig.show()

ÉQUIPEMENT DE SÉCURITÉ × TYPE D'USAGER → GRAVITÉ

Conducteur :
  Avec ceinture :  217,252 → 9.7% grave
  Sans ceinture :  139,246 → 27.2% grave
  Ratio sans/avec : 2.8x

Passager :
  Avec ceinture :   62,693 → 13.6% grave
  Sans ceinture :   22,143 → 24.4% grave
  Ratio sans/avec : 1.8x


### Observation : Équipement de sécurité

**Analyse INTRA-GROUPE** (la seule qui élimine le confounding) :

| Rôle | Avec ceinture | Sans ceinture | Ratio sans/avec |
|------|--------------|---------------|-----------------|
| **Conducteur** | 9.7% | **27.2%** | **2.8x** |
| **Passager** | 13.6% | **24.4%** | **1.8x** |

**Conclusion** : L'absence de ceinture multiplie le risque par **2.8x pour les conducteurs** et **1.8x pour les passagers**. C'est un effet protecteur RÉEL et massif, bien documenté dans la littérature (réduction de 45-50% de la mortalité selon l'OMS).

**Paradoxe résolu** : Quand on compare intra-groupe (conducteurs entre eux), la ceinture est clairement protectrice. La corrélation négative globale (-0.223) mélange deux effets : (1) la protection réelle de la ceinture et (2) le fait que les porteurs de ceinture sont en voiture (véhicule protégé).

**Pour l'interprétation épidémiologique** : distinguer la causalité (ceinture protège) de la corrélation (ceinture = proxy voiture) sera important dans les conclusions du modèle.

### 4.3 Corrélations des features usager avec la target

In [10]:
# Corrélations de TOUTES les features avec grave_usager
all_features = [c for c in df.columns if c != 'grave_usager']

correlations = pd.Series(
    {feat: df[feat].corr(df['grave_usager']) for feat in all_features}
).sort_values(key=abs, ascending=False)

print("="*60)
print("TOP 20 CORRÉLATIONS AVEC grave_usager")
print("="*60)
for i, (feat, corr) in enumerate(correlations.head(20).items(), 1):
    # Marquer les features usager
    user_feat = user_features_demo + user_features_comportement
    marker = " ★" if feat in user_feat else ""
    print(f"{i:>2}. {feat:<30} {corr:>+.3f}{marker}")

print("\n★ = feature usager (nouvelle par rapport au niveau accident)")

# Visualisation : top 15 corrélations
top_corr = correlations.head(15)
colors = ['#e74c3c' if feat in user_features_demo + user_features_comportement else '#3498db' 
          for feat in top_corr.index]

fig = go.Figure(go.Bar(
    y=top_corr.index[::-1],
    x=top_corr.values[::-1],
    orientation='h',
    marker_color=colors[::-1],
    text=[f'{v:+.3f}' for v in top_corr.values[::-1]],
    textposition='outside'
))

fig.add_vline(x=0, line_dash='dash', line_color='gray')
fig.update_layout(
    title='Top 15 corrélations avec grave_usager (rouge = feature usager)',
    xaxis_title='Corrélation',
    height=500
)
fig.show()

TOP 20 CORRÉLATIONS AVEC grave_usager
 1. ceinture                       -0.223 ★
 2. casque                         +0.195 ★
 3. obstacle_fixe_dur              +0.184
 4. route_departementale           +0.178
 5. hors_agglo                     +0.166
 6. nb_vehicules                   -0.151
 7. bidirectionnelle               +0.144
 8. obstacle_arbre                 +0.131
 9. trajet_loisir                  +0.130 ★
10. collision_solo                 +0.129
11. route_communale                -0.127
12. pieton_usager                  +0.107 ★
13. age_65_plus                    +0.105 ★
14. vma                            +0.105
15. lat                            -0.100
16. collision_cote                 -0.091
17. collision_arriere              -0.091
18. nb_usagers                     -0.090
19. nuit_non_eclairee              +0.088
20. sans_protection                +0.086 ★

★ = feature usager (nouvelle par rapport au niveau accident)


### Observation : Corrélations

**Top 5 corrélations avec `grave_usager`** :

| Rang | Feature | Corrélation | Type |
|------|---------|-------------|------|
| 1 | `ceinture` | **-0.223** | ★ Usager |
| 2 | `casque` | +0.195 | ★ Usager (confondant) |
| 3 | `obstacle_fixe_dur` | +0.184 | Accident |
| 4 | `route_departementale` | +0.178 | Accident |
| 5 | `hors_agglo` | +0.166 | Accident |

**Résultat clé** : `ceinture` est LA feature **la plus prédictive** du dataset, devant toutes les features accident. Cela **valide le choix de la granularité usager** pour l'analyse épidémiologique.

**6 des 20 top features sont des features usager** (★) :
- `ceinture` (-0.223), `casque` (+0.195), `trajet_loisir` (+0.130)
- `pieton_usager` (+0.107), `age_65_plus` (+0.105), `sans_protection` (+0.086)

**⚠️ Alerte confounding** : `casque` (+0.195) est la 2ème corrélation. Mais comme démontré en section 4, c'est un proxy de "deux-roues motorisé", pas un facteur de risque. Le modèle utilisera cette corrélation pour prédire, ce qui est correct en prédiction, mais **faux en interprétation causale**.

---

## 5. Datasets progressifs

### Versions

| Version | Contenu | Features ajoutées |
|---------|---------|-------------------|
| **V1** | Contexte + Démographie | 23 accident context + 7 user demo |
| **V2** | + Véhicules + Comportement | + 9 vehicle types + 4 counts + 5 user behavior |
| **V3** | Complet | + 4 collision types + 3 obstacles + 1 interaction |

In [11]:
# === V1 : CONTEXTE + DÉMOGRAPHIE ===

# Features contexte accident (même que 04b V1)
features_contexte = [
    'lat', 'long', 'heure', 'jour_semaine', 'mois',
    'weekend', 'nuit', 'heure_pointe', 'heure_danger',
    'nuit_non_eclairee', 'nuit_eclairee',
    'vma', 'nbv',
    'hors_agglo', 'bidirectionnelle', 'haute_vitesse',
    'route_autoroute', 'route_nationale', 'route_departementale', 'route_communale', 'route_rapide',
    'nuit_hors_agglo', 'weekend_nuit'
]

# Features démographie usager
features_demo = ['age', 'homme', 'conducteur', 'passager', 'pieton_usager', 'age_18_24', 'age_65_plus']

target = 'grave_usager'

v1_features = features_contexte + features_demo
v1_cols = v1_features + [target]

# Vérification
missing = [c for c in v1_cols if c not in df.columns]
assert not missing, f"Colonnes manquantes V1 : {missing}"

df_v1 = df[v1_cols].copy()

print("="*60)
print("V1 - CONTEXTE + DÉMOGRAPHIE")
print("="*60)
print(f"Shape : {df_v1.shape}")
print(f"Features contexte   : {len(features_contexte)}")
print(f"Features démographie : {len(features_demo)}")
print(f"Total features      : {len(v1_features)}")
print(f"\nValeurs manquantes : {df_v1.isna().sum().sum()}")

# Corrélations V1
corr_v1 = pd.Series({f: df_v1[f].corr(df_v1[target]) for f in v1_features}).sort_values(key=abs, ascending=False)
print("\nTop 5 corrélations V1 :")
for feat, corr in corr_v1.head(5).items():
    print(f"  {feat:<30} {corr:>+.3f}")
print(f"\nCorr max : {corr_v1.abs().max():.3f}")

V1 - CONTEXTE + DÉMOGRAPHIE
Shape : (477294, 31)
Features contexte   : 23
Features démographie : 7
Total features      : 30

Valeurs manquantes : 0

Top 5 corrélations V1 :
  route_departementale           +0.178
  hors_agglo                     +0.166
  bidirectionnelle               +0.144
  route_communale                -0.127
  pieton_usager                  +0.107

Corr max : 0.178


### Observation : V1

- **30 features** (23 contexte + 7 démographie), 477,294 lignes, 0 missing
- **Corr max = 0.178** (`route_departementale`)
- Les features usager `pieton_usager` (+0.107) et `age_65_plus` (+0.105) entrent dans le top 5

Par rapport à 04b V1 (accident-level) qui avait corr max = 0.259, la V1 usager a un signal plus faible (0.178). C'est attendu : le signal se dilue quand on passe d'un accident à ses usagers individuels.

In [12]:
# === V2 : + VÉHICULES + COMPORTEMENT ===

# Features véhicules (accident-level)
features_vehicules = [
    'has_moto', 'has_velo', 'has_edp', 'has_cyclomoteur', 'has_pieton',
    'has_vulnerable', 'has_poids_lourd', 'has_bus', 'has_vehicule_lourd',
    'nb_vehicules', 'nb_usagers', 'nb_pietons',
    'age_moyen',
]

# Features comportement usager
features_comportement = ['ceinture', 'casque', 'sans_protection', 'trajet_domicile_travail', 'trajet_loisir']

v2_features = v1_features + features_vehicules + features_comportement
v2_cols = v2_features + [target]

missing = [c for c in v2_cols if c not in df.columns]
assert not missing, f"Colonnes manquantes V2 : {missing}"

df_v2 = df[v2_cols].copy()

print("="*60)
print("V2 - + VÉHICULES + COMPORTEMENT")
print("="*60)
print(f"Shape : {df_v2.shape}")
print(f"Features V1         : {len(v1_features)}")
print(f"+ Véhicules         : {len(features_vehicules)}")
print(f"+ Comportement      : {len(features_comportement)}")
print(f"Total features      : {len(v2_features)}")
print(f"\nValeurs manquantes : {df_v2.isna().sum().sum()}")

# Nouvelles corrélations V2
new_v2 = features_vehicules + features_comportement
corr_v2_new = pd.Series({f: df_v2[f].corr(df_v2[target]) for f in new_v2}).sort_values(key=abs, ascending=False)
print("\nTop 5 nouvelles corrélations V2 :")
for feat, corr in corr_v2_new.head(5).items():
    print(f"  {feat:<30} {corr:>+.3f}")

# Gain V1 → V2
corr_v1_max = corr_v1.abs().max()
corr_v2_all = pd.Series({f: df_v2[f].corr(df_v2[target]) for f in v2_features})
corr_v2_max = corr_v2_all.abs().max()
print(f"\nCorr max V1 : {corr_v1_max:.3f} → V2 : {corr_v2_max:.3f} (gain : {(corr_v2_max-corr_v1_max)/corr_v1_max*100:+.0f}%)")

V2 - + VÉHICULES + COMPORTEMENT
Shape : (477294, 49)
Features V1         : 30
+ Véhicules         : 13
+ Comportement      : 5
Total features      : 48

Valeurs manquantes : 0

Top 5 nouvelles corrélations V2 :
  ceinture                       -0.223
  casque                         +0.195
  nb_vehicules                   -0.151
  trajet_loisir                  +0.130
  nb_usagers                     -0.090

Corr max V1 : 0.178 → V2 : 0.223 (gain : +25%)


### Observation : V2

- **48 features** (V1 + 13 véhicules + 5 comportement), 0 missing
- **Corr max = 0.223** (`ceinture`) → **gain +25% par rapport à V1**
- Le gain vient des features usager (`ceinture`, `casque`, `trajet_loisir`), pas des features véhicules accident

**V1 → V2 : le saut le plus important**, comme pour UC1 en 04a. La `ceinture` devient la feature #1 du dataset, devant toutes les features accident.

**Ce résultat confirme la valeur ajoutée de la granularité usager** : les features individuelles apportent un gain de +25% en pouvoir prédictif par rapport au contexte accident seul.

In [13]:
# === V3 : COMPLET ===

# Features post-accident
features_post_accident = [
    'collision_frontale', 'collision_arriere', 'collision_cote', 'collision_solo',
    'obstacle_arbre', 'obstacle_fixe_dur', 'obstacle_pieton',
    'collision_asymetrique',
]

v3_features = v2_features + features_post_accident
v3_cols = v3_features + [target]

missing = [c for c in v3_cols if c not in df.columns]
assert not missing, f"Colonnes manquantes V3 : {missing}"

df_v3 = df[v3_cols].copy()

print("="*60)
print("V3 - COMPLET")
print("="*60)
print(f"Shape : {df_v3.shape}")
print(f"Features V2         : {len(v2_features)}")
print(f"+ Post-accident     : {len(features_post_accident)}")
print(f"Total features      : {len(v3_features)}")
print(f"\nValeurs manquantes : {df_v3.isna().sum().sum()}")

# Nouvelles corrélations V3
corr_v3_new = pd.Series({f: df_v3[f].corr(df_v3[target]) for f in features_post_accident}).sort_values(key=abs, ascending=False)
print("\nNouvelles corrélations V3 :")
for feat, corr in corr_v3_new.items():
    print(f"  {feat:<30} {corr:>+.3f}")

# Gain V2 → V3
corr_v3_all = pd.Series({f: df_v3[f].corr(df_v3[target]) for f in v3_features})
corr_v3_max = corr_v3_all.abs().max()
print(f"\nCorr max V2 : {corr_v2_max:.3f} → V3 : {corr_v3_max:.3f} (gain : {(corr_v3_max-corr_v2_max)/corr_v2_max*100:+.0f}%)")

V3 - COMPLET
Shape : (477294, 57)
Features V2         : 48
+ Post-accident     : 8
Total features      : 56

Valeurs manquantes : 0

Nouvelles corrélations V3 :
  obstacle_fixe_dur              +0.184
  obstacle_arbre                 +0.131
  collision_solo                 +0.129
  collision_cote                 -0.091
  collision_arriere              -0.091
  collision_frontale             +0.084
  collision_asymetrique          +0.015
  obstacle_pieton                -0.012

Corr max V2 : 0.223 → V3 : 0.223 (gain : +0%)


### Observation : V3

- **56 features** (V2 + 8 post-accident), 0 missing
- **Corr max = 0.223** → **gain +0% par rapport à V2**

**Constat** : Les features post-accident (obstacles, collisions) **n'apportent aucun gain marginal** au-dessus de `ceinture`. La feature `obstacle_fixe_dur` (+0.184) est la plus forte des nouvelles features mais reste en dessous de `ceinture` (-0.223).

**Implication pour la modélisation** : La V2 pourrait être suffisante. Les 8 features post-accident ajoutent de la dimensionnalité sans gain en corrélation max. Cependant, elles pourraient apporter un gain non-linéaire (interactions) que la corrélation linéaire ne capture pas. → À tester avec le modèle.

---

## 6. Comparaison accident-level vs usager-level

In [14]:
# Charger le dataset accident-level UC2 V3 pour comparaison
df_accident_uc2 = pd.read_csv(DATA_DIR / 'UC2_v3_complet.csv')

print("="*70)
print("COMPARAISON ACCIDENT-LEVEL vs USAGER-LEVEL")
print("="*70)

print(f"\n{'Métrique':<35} {'Accident (04b)':>15} {'Usager (04c)':>15}")
print("-"*65)
print(f"{'Lignes':<35} {len(df_accident_uc2):>15,} {len(df_v3):>15,}")
print(f"{'Features':<35} {df_accident_uc2.shape[1]-1:>15} {df_v3.shape[1]-1:>15}")

target_acc = 'grave'
rate_acc = df_accident_uc2[target_acc].mean() * 100
rate_usr = df_v3['grave_usager'].mean() * 100
print(f"{'Taux de gravité':<35} {rate_acc:>14.1f}% {rate_usr:>14.1f}%")

ratio_acc = (1 - df_accident_uc2[target_acc].mean()) / df_accident_uc2[target_acc].mean()
ratio_usr = (1 - df_v3['grave_usager'].mean()) / df_v3['grave_usager'].mean()
print(f"{'Ratio négatifs:positifs':<35} {'1:' + f'{ratio_acc:.1f}':>15} {'1:' + f'{ratio_usr:.1f}':>15}")

# Features communes
common_features = [c for c in df_accident_uc2.columns if c in df_v3.columns and c not in ['grave', 'grave_usager', 'mortel']]

# Top corrélations comparées
print(f"\n{'Feature':<30} {'Corr Accident':>15} {'Corr Usager':>15} {'Diff':>8}")
print("-"*70)

comparison = []
for feat in common_features:
    corr_acc = df_accident_uc2[feat].corr(df_accident_uc2[target_acc])
    corr_usr = df_v3[feat].corr(df_v3['grave_usager'])
    comparison.append((feat, corr_acc, corr_usr, abs(corr_usr) - abs(corr_acc)))

comparison.sort(key=lambda x: abs(x[2]), reverse=True)
for feat, corr_acc, corr_usr, diff in comparison[:15]:
    print(f"{feat:<30} {corr_acc:>+15.3f} {corr_usr:>+15.3f} {diff:>+8.3f}")

# Features usager-only
user_only = [c for c in df_v3.columns if c not in df_accident_uc2.columns and c != 'grave_usager']
if user_only:
    print(f"\nFeatures EXCLUSIVES au niveau usager ({len(user_only)}) :")
    for feat in user_only:
        corr = df_v3[feat].corr(df_v3['grave_usager'])
        print(f"  {feat:<30} {corr:>+.3f}")

COMPARAISON ACCIDENT-LEVEL vs USAGER-LEVEL

Métrique                             Accident (04b)    Usager (04c)
-----------------------------------------------------------------
Lignes                                      208,616         477,294
Features                                         46              56
Taux de gravité                               35.4%           17.7%
Ratio négatifs:positifs                       1:1.8           1:4.7

Feature                          Corr Accident     Corr Usager     Diff
----------------------------------------------------------------------
obstacle_fixe_dur                       +0.199          +0.184   -0.015
route_departementale                    +0.259          +0.178   -0.081
hors_agglo                              +0.257          +0.166   -0.091
nb_vehicules                            -0.129          -0.151   +0.022
bidirectionnelle                        +0.203          +0.144   -0.059
obstacle_arbre                          +0.137

In [15]:
# Visualisation : scatter corrélations accident vs usager
df_comp = pd.DataFrame(comparison, columns=['feature', 'corr_accident', 'corr_usager', 'diff'])

fig = px.scatter(
    df_comp, x='corr_accident', y='corr_usager',
    text='feature', color='diff',
    color_continuous_scale='RdBu_r',
    title='Corrélations : niveau accident vs niveau usager (features communes)'
)

# Ligne y=x (corrélations identiques)
min_val = min(df_comp['corr_accident'].min(), df_comp['corr_usager'].min()) - 0.02
max_val = max(df_comp['corr_accident'].max(), df_comp['corr_usager'].max()) + 0.02
fig.add_trace(go.Scatter(
    x=[min_val, max_val], y=[min_val, max_val],
    mode='lines', line=dict(dash='dash', color='gray'),
    showlegend=False
))

fig.update_traces(textposition='top center', textfont_size=8, selector=dict(mode='markers+text'))
fig.update_layout(
    height=600, width=700,
    xaxis_title='Corrélation avec GRAVE (accident)',
    yaxis_title='Corrélation avec GRAVE_USAGER (usager)'
)
fig.show()

### Observation : Comparaison accident vs usager

| Métrique | Accident (04b) | Usager (04c) |
|----------|----------------|--------------|
| **Lignes** | 208,616 | 477,294 (×2.3) |
| **Features** | 46 | 56 (+12 usager) |
| **Taux de gravité** | 35.4% | **17.7%** |
| **Ratio** | 1:1.8 | **1:4.7** |

**Corrélations systématiquement plus faibles au niveau usager** : La plupart des features accident ont un diff négatif. C'est un phénomène de **dilution du signal** : quand un accident grave contient 3 usagers dont 1 grave et 2 indemnes, la corrélation accident→gravité est forte (1/1 = 100%) mais usager→gravité est faible (1/3 = 33%).

**Exceptions** (signal renforcé au niveau usager) :
- `nb_vehicules` : diff +0.022 → plus de véhicules = plus d'usagers non blessés
- `collision_solo` : diff +0.039 → en solo, l'unique usager est souvent le blessé
- `nb_usagers` : diff +0.054 → plus d'usagers = plus de dilution du risque individuel

**Features exclusives usager** : 12 features non disponibles au niveau accident, dont `ceinture` (-0.223) qui est **la feature #1 du dataset**. C'est le principal argument pour le passage à la granularité usager.

---

## 7. Sauvegarde des datasets

In [16]:
# Sauvegarder les 3 versions
datasets = {
    'UC2_usager_v1_demo.csv': df_v1,
    'UC2_usager_v2_comportement.csv': df_v2,
    'UC2_usager_v3_complet.csv': df_v3,
}

print("="*60)
print("SAUVEGARDE DES DATASETS")
print("="*60)

for filename, dataset in datasets.items():
    filepath = DATA_DIR / filename
    dataset.to_csv(filepath, index=False)
    n_features = dataset.shape[1] - 1
    print(f"\n✓ {filename}")
    print(f"  Shape    : {dataset.shape}")
    print(f"  Features : {n_features}")
    print(f"  Missing  : {dataset.isna().sum().sum()}")
    print(f"  Target   : {dataset['grave_usager'].sum():,} ({dataset['grave_usager'].mean()*100:.1f}%)")

SAUVEGARDE DES DATASETS

✓ UC2_usager_v1_demo.csv
  Shape    : (477294, 31)
  Features : 30
  Missing  : 0
  Target   : 84,329 (17.7%)

✓ UC2_usager_v2_comportement.csv
  Shape    : (477294, 49)
  Features : 48
  Missing  : 0
  Target   : 84,329 (17.7%)

✓ UC2_usager_v3_complet.csv
  Shape    : (477294, 57)
  Features : 56
  Missing  : 0
  Target   : 84,329 (17.7%)


In [17]:
# Résumé final
print("\n" + "="*70)
print("RÉSUMÉ COMPARATIF DES VERSIONS")
print("="*70)

print(f"\n{'Version':<15} {'Features':>10} {'Lignes':>12} {'Taux grave':>12} {'Corr max':>10}")
print("-"*60)

for name, dataset, features in [
    ('V1 Demo', df_v1, v1_features),
    ('V2 Comport.', df_v2, v2_features),
    ('V3 Complet', df_v3, v3_features),
]:
    n_feat = len(features)
    n_rows = len(dataset)
    rate = dataset['grave_usager'].mean() * 100
    corr_max = max(abs(dataset[f].corr(dataset['grave_usager'])) for f in features)
    print(f"{name:<15} {n_feat:>10} {n_rows:>12,} {rate:>11.1f}% {corr_max:>10.3f}")

# Comparaison avec accident-level
print("\n" + "-"*60)
print(f"{'04b V3 (acc.)':<15} {df_accident_uc2.shape[1]-1:>10} {len(df_accident_uc2):>12,} {df_accident_uc2['grave'].mean()*100:>11.1f}% {'':>10}")


RÉSUMÉ COMPARATIF DES VERSIONS

Version           Features       Lignes   Taux grave   Corr max
------------------------------------------------------------
V1 Demo                 30      477,294        17.7%      0.178
V2 Comport.             48      477,294        17.7%      0.223
V3 Complet              56      477,294        17.7%      0.223

------------------------------------------------------------
04b V3 (acc.)           46      208,616        35.4%           


---

## Observations et conclusions

### 1. Dataset usager créé

- **477,294 usagers** × 56 features (V3 complète)
- Target `grave_usager` = 17.7% (84,329 usagers tués ou hospitalisés)
- **0 valeurs manquantes** dans les 3 versions

### 2. Changement de paradigme par rapport au niveau accident

| Aspect | Accident (04b) | Usager (04c) | Impact |
|--------|----------------|--------------|--------|
| Volume | 208k | 477k | ×2.3 plus de données |
| Taux gravité | 35.4% | 17.7% | Divisé par 2 |
| Ratio | 1:1.8 | 1:4.7 | Plus déséquilibré |
| Feature #1 | `route_departementale` (0.259) | `ceinture` (-0.223) | Individuel > contextuel |

### 3. Features usager les plus prédictives

| Feature | Corrélation | Interprétation |
|---------|-------------|----------------|
| `ceinture` | **-0.223** | Facteur protecteur #1 (mais aussi proxy "voiture") |
| `casque` | +0.195 | **Confondant** : proxy "deux-roues" (Simpson's paradox) |
| `trajet_loisir` | +0.130 | Loisirs = plus de deux-roues, alcool |
| `pieton_usager` | +0.107 | 32% de gravité (1.8× baseline) |
| `age_65_plus` | +0.105 | 29% de gravité (1.6× baseline) |

### 4. Points critiques

**a) Paradoxe de Simpson sur `casque`** : La 2ème corrélation du dataset est un **artefact de confounding**. Les casqués sont des motards, intrinsèquement plus vulnérables. Le modèle utilisera `casque` comme proxy de "deux-roues", ce qui est valide en prédiction mais **faux en interprétation causale**. L'analyse intra-groupe (conducteurs avec/sans ceinture : 9.7% vs 27.2%) est la seule qui isole l'effet protecteur réel.

**b) Feature `sans_protection` bruitée** : 23.3% inclut les piétons (pas de ceinture/casque applicable), les non-renseignés (-1) et les "autres" (9). Ce n'est pas un indicateur fiable d'absence volontaire de protection.

**c) Déséquilibre plus marqué** : Le ratio 1:4.7 (vs 1:1.8 au niveau accident) nécessite une attention particulière. BalancedBagging ou class_weight='balanced' restent adaptés mais le seuil de décision devra être calibré.

**d) Dilution du signal** : Les corrélations accident→gravité sont systématiquement plus faibles au niveau usager. Le modèle aura besoin de plus de données (ce qu'on a : ×2.3) pour compenser.

### 5. Progression des versions

| Version | Features | Corr max | Gain | Commentaire |
|---------|----------|----------|------|-------------|
| V1 Demo | 30 | 0.178 | - | Contexte + démographie |
| **V2 Comport.** | **48** | **0.223** | **+25%** | **Saut majeur grâce à `ceinture`** |
| V3 Complet | 56 | 0.223 | +0% | Pas de gain marginal en corrélation |

**Recommandation** : Tester V2 ET V3 en modélisation. V2 pourrait suffire, mais V3 peut apporter des interactions non-linéaires invisibles en corrélation.

### 6. Prochaine étape

→ **05b_model_UC2_epidemio.ipynb** : Modélisation UC2 (target `grave_usager`, BalancedBagging, datasets V2/V3)